In [500]:
import requests
from selenium.webdriver import (Chrome, Firefox, ChromeOptions, FirefoxProfile)
import pymongo
import datetime
from bs4 import BeautifulSoup
import pandas as pd
import yaml
import time
import random

In [501]:
# Variables
path_to_fb_login_yaml = "/Users/jasonli/.secrets/facebook-web-scrape-cred.yaml"
my_profile_url = "https://www.facebook.com/jason.li.96930"

In [502]:
# Initialize MongoDB
mc = pymongo.MongoClient()
db = mc['my-facebook-webscrape']
fb_statuses = db['fb-statuses']

In [553]:
# Read FB Credentials
with open(path_to_fb_login_yaml, 'r') as stream:
    try:
        y = yaml.load(stream)
        my_password = y['password']
        my_email = y['email']
    except yaml.YAMLError as exc:
        print(exc)

In [605]:
# Choose a Browser:

# CHROME
# options = ChromeOptions();
# options.add_argument("--disable-notifications");

# browser = Chrome(options=options)

# FIREFOX
profile = FirefoxProfile();
profile.set_preference("dom.webnotifications.enabled", False);
browser = Firefox(firefox_profile=profile)

In [613]:
# Login to FB in Selenium Browser
url = 'https://www.facebook.com/'
browser.get(url)

email = browser.find_element_by_id('email')
password = browser.find_element_by_id('pass')

email.send_keys(my_email)
password.send_keys(my_password)

browser.find_element_by_id("loginbutton").click()

ConnectionRefusedError: [Errno 61] Connection refused

In [611]:
# Navigate to the friends tab in your profile
browser.find_element_by_css_selector(f'a[href="{my_profile_url}"]').click()
time.sleep(2)

browser.find_element_by_css_selector('a[data-tab-key="friends"]').click()
time.sleep(2)

number_of_friends = int(browser.find_element_by_name('All Friends').find_elements_by_css_selector('span')[1].text)
print('Number of friends: ' + str(number_of_friends))

ConnectionRefusedError: [Errno 61] Connection refused

In [296]:
# Create a dictionary of friends and profile_urls,
# where key=friend_name and value=friend_profile_url 
SCROLL_PAUSE_TIME = 1

# Get scroll height
last_height = browser.execute_script("return document.body.scrollHeight")

friends_profiles_dict = {}

while len(friends_profiles_dict.items()) < number_of_friends:

    # Scroll down to bottom
    browser.execute_script("window.scrollTo(0, document.body.scrollHeight);")

    # Wait to load page
    time.sleep(SCROLL_PAUSE_TIME)
    
    
    friend_items = browser.find_elements_by_css_selector('div[data-testid=friend_list_item]')
    
    if len(friends_profiles_dict.items()) > number_of_friends:
        break
    
    for friend_item in friend_items:
        profile_links = friend_item.find_elements_by_css_selector('a')
            
        for profile in profile_links:
            url = profile.get_attribute('href')
            
            if (
                my_profile_url not in url and 
                '?' in url and 
                'browse/mutual_friends/' not in url
            ):
                if not any(char.isdigit() for char in profile.text) or not profile.text:
                    if 'profile.php?id=' in url:
                        friends_profiles_dict[profile.text] = url
                    else:
                        s = url.split('?')[0]
                        friends_profiles_dict[profile.text] = s
            
    print('Creating friends dictionary... \n Friend count: ' +  str(len(friends_profiles_dict.items())) + ' friends.')

    # Calculate new scroll height and compare with last scroll height
    new_height = browser.execute_script("return document.body.scrollHeight")
    if new_height == last_height:
        print('Finished creating friends dictionary!')
        break
    last_height = new_height

21
41
81
101
120
139
158
175
194
214
234
254
254
293
313
332
352
372
391
402
402
402
402
402
402
402
402


In [590]:
# Remove blank values
friends_profiles_dict = {k: v for k, v in friends_profiles_dict.items() if k is not ''}
friends_profiles_dict

{'Adam Koehler': 'https://www.facebook.com/adam.koehler.50',
 'Adanimo Nrg': 'https://www.facebook.com/adam.arguello.35',
 'Adelina Manaut': 'https://www.facebook.com/adelinamanaut',
 'Alana McKnight': 'https://www.facebook.com/alanajoy93',
 'Alannah Rose': 'https://www.facebook.com/alannahnahnah',
 'Alex Beaton': 'https://www.facebook.com/alex.beaton.988',
 'Alex Chang': 'https://www.facebook.com/changAlang24',
 'Alex Grob': 'https://www.facebook.com/Grob.Alex',
 'Alex Keeno': 'https://www.facebook.com/akeeno11',
 'Alexander Cheung': 'https://www.facebook.com/alexander.cheung.564',
 'Alexander Hooton': 'https://www.facebook.com/alexander.hooton.5',
 'Alexander Pang': 'https://www.facebook.com/alexander.pang.5',
 'Alexander Robinson': 'https://www.facebook.com/PRIDE908',
 'Alexis Szigeti': 'https://www.facebook.com/alexismarieszigeti',
 'Alfred Quaicoe': 'https://www.facebook.com/fred.amissah',
 'Ali Patton': 'https://www.facebook.com/ali.patton.12',
 'Ally Holtz': 'https://www.faceboo

In [ ]:
already_scraped = {
    'Kellian Valenti': 'https://www.facebook.com/kpv093',
    'Chen Chi': 'https://www.facebook.com/Melodycc55',
    'Jonathan Cheung': 'https://www.facebook.com/jonathan.cheung.545',
    'Sybil Cheng': 'https://www.facebook.com/sybil.cheng1',
}

In [ ]:
friends_to_scrape_keys = set(friends_profiles_dict.keys()) - set(already_scraped.keys())

friends_to_scrape = {}
for key in friends_to_scrape_keys:
    friends_to_scrape[key] = friends_profiles_dict[key]

In [610]:
# Web scrape each friend in friends dictionary, add statuses to mongoDB.
# Data structure of each entry:
#   {'name': STRING = name,
#   'url': STRING = profile url,
#   'datetime': DATETIME = current time,
#   'statuses': DICT = {key=time of status post, value=status}, 
#   'html': STRING = html of page,}

number_of_statuses = 200

min_scroll_time = 3

# Iterate through each friend in the friends dictionary
for name, url in mod_friends_profiles_dict.items():
    person_dict = fb_statuses.find_one({"url": url})
    
#     if person not in DB
    if person_dict == None:
        statuses_dict = {}
    else:
        statuses_dict = person_dict['statuses']
    
    browser.get(url)

    # Get scroll height
    last_height = browser.execute_script("return document.body.scrollHeight")

    
    # Scroll through friends timeline and add statuses to dictionary    
    while len(statuses_dict.items()) < number_of_statuses:

        SCROLL_PAUSE_TIME = min_scroll_time * (1 + random.random())

        # Scroll down to bottom
        browser.execute_script("window.scrollTo(0, document.body.scrollHeight);")

        # Wait to load page
        time.sleep(SCROLL_PAUSE_TIME)
        
        posts = browser.find_elements_by_css_selector('div[id*=tl_unit]')
        
        for post in posts:
            try:
                post_time_element = post.find_element_by_css_selector('abbr')
                post_time = post_time_element.get_attribute('title')
                post_context = post.find_element_by_css_selector('h5')
            
                # Conditionals to weed out non authored posts
                if (post_time not in statuses_dict.keys() and
                    name in post_context.text and
                    'is with' not in post_context.text and
                    'was tagged' not in post_context.text and
                    'is in' not in post_context.text and
                    'to' not in post_context.text): 

                    user_content_element = post.find_element_by_css_selector('div[class*=userContent]')
                    para_elements = user_content_element.find_elements_by_css_selector('p')

                    # Status sometimes split in two p elements. Merge two paragraphs
                    if len(para_elements) > 0:
                        text = ''
                        for para_element in para_elements:
                            text += para_element.text + ' '

                    print('Time: ' + post_time + '\n' + 'Status: ' + text + '\n')

                    # Add status to dictionary
                    statuses_dict[post_time] = text
            except:
                print('Something Not Found')
        print('Creating statuses dictionary for ' + name + '... \n' + 'Status count: ' +  str(len(statuses_dict.items())) + ' statuses.')
        

        # Calculate new scroll height and compare with last scroll height
        new_height = browser.execute_script("return document.body.scrollHeight")
        
        # Reached the end of friend's timeline, add name to already_scraped_dict
        if new_height == last_height:
            print('Finished creating ' + name + ' statuses dictionary!')
            already_scraped_dict[name] = url
            break
        last_height = new_height
        
    html = browser.page_source
    
    # Add entry to MongoDB
    fb_statuses.update_one(
        {'url': url}, 
        {'$set': {
            'name': name,
            'url': url,
            'datetime': datetime.datetime.now(),
            'statuses': statuses_dict, 
            'html': html, 
            }
        },
    upsert=True
    )

ConnectionRefusedError: [Errno 61] Connection refused

In [616]:
fb_statuses.count()

401

In [ ]:
fb_statuses.insert()

In [627]:
fb_statuses.find_one({'url': {'$exists': True}})

{'_id': ObjectId('5af34452ebd4d7fef64d24da'),
 'datetime': datetime.datetime(2018, 5, 10, 2, 1, 44, 775000),
 'html': '<html id="facebook" class="sidebarMode" lang="en"><head><meta charset="utf-8"><meta name="referrer" content="origin-when-crossorigin" id="meta_referrer"><script>window._cstart=+new Date();</script>                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            

In [624]:
fb_statuses.distinct('statuses')


[{'08/03/2009 9:20pm': "I'm done (╯°□°）╯︵ ┻━┻) "},
 {'01/01/2017 8:55am': "Wasted too much time on taking a picture of the little squirrel( Shouldn't they have being hibernated?) ",
  '01/02/2018 7:43am': 'May we be at peace.\nBegin New Year with standing on the top of Rock. ',
  '01/04/2017 7:57am': 'Veggie Fries 4 Ways\nFULL RECIPES: http://bzfd.it/2iEL0Jv ',
  '01/04/2017 8:01am': 'Chinese homemade cuisine Names:\n山芋烧牛\n虎皮青椒...  ',
  '01/07/2017 3:01pm': 'Snowy day ~ ',
  '01/08/2018 5:26pm': '板栗烧鸡 ',
  '01/11/2018 12:47pm': '油腻少女范儿get! @ Chelsea, Manhattan ',
  '01/12/2018 7:11pm': '油腻少女范儿get! @ Chelsea, Manhattan ',
  '01/12/2018 7:18pm': 'Amazing Samsung~ ',
  '01/14/2017 3:29pm': 'Photographed in 2015\nThe Forbidden City ',
  '01/16/2017 4:20pm': '多年前对纽约的第一印象是这里 ',
  '01/21/2017 8:05am': 'Fireworks for Chinese new year~! ',
  '01/27/2017 2:51pm': 'Fireworks for Chinese new year~! ',
  '01/28/2017 7:45am': '努力把生活点缀的好一些些～ ',
  '02/04/2017 12:15pm': 'Shrimp,dark rum, vanilla extrac

In [593]:
fb_statuses.find_one()

{'_id': ObjectId('5af34452ebd4d7fef64d24da'),
 'datetime': datetime.datetime(2018, 5, 9, 11, 56, 18, 385000),
 'html': '<html id="facebook" class="sidebarMode" lang="en"><head><meta charset="utf-8"><meta name="referrer" content="origin-when-crossorigin" id="meta_referrer"><script>window._cstart=+new Date();</script>                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                           

In [474]:
list(fb_statuses.aggregate([
    {"$group" : { "_id": "$name", "count": { "$sum": 1 } } },
    {"$match": {"_id" :{ "$ne" : None } , "count" : {"$gt": 1} } }] ))
#     {"$sort": {"count" : -1} },
#     {"$project": {"name" : "$_id", "_id" : 0} }     
# )

[{'_id': 'Bradley Li', 'count': 2}]

{'02/08/2018 10:32pm': "*cough cough hint hint*\nYour weekly dose of interesting posts brought to you by me and Amy Isn't It True 😂 ( via Edinburgh Zoo ) ",
 '03/11/2016 3:26pm': "Not sure if I want this game. It looks fun but it doesn't look like it will fill my fps void. Your watch is about to begin—Overwatch arrives May 24! Are you with us? blizz.ly/BuyOverwatch ",
 '06/01/2015 5:02am': '"Here\'s to those olden days,\nHere\'s to those golden days,\nHere\'s to the friends we made at dear old RPI." Gross, I can\'t believe I just quoted our alma mater. Anyways, thanks for making the last 4 years pretty great, BARH Settlement. Google Maps keeps asking me to set 16th St as "Home", and I\'m inclined to click yes. But we kind of moved out. So maybe not. Also, I\'m a =π€®°^¥. Ahem. I\'m a human. My tail didn\'t just slip.  ',
 '06/26/2015 12:51am': 'Noodles no back, bubble shield... even bubble shield on the trash can :P Ha! Even in Taiwan! ',
 '11/08/2015 11:26am': 'Hello!',
 '11/08/2016 3

1

{'01/01/2014 3:04am': 'HAPPY NEW YEARS!! Pop pop pop...man I miss doing fireworks ',
 '01/01/2015 3:01am': 'Happy new years ',
 '01/01/2016 3:09am': "Happy new years 2015 was OK let's hope 2016 will be even better ",
 '01/01/2017 8:23am': 'Happy new years I traveled into the future to deliver this message ',
 '01/08/2015 9:59pm': 'Shaboo shaboo ',
 '01/09/2016 12:43am': 'Close game that kick though ',
 '01/11/2014 7:11pm': 'getting wisdoms pulled sucks ',
 '01/11/2016 10:23pm': 'Close game that kick though ',
 '01/13/2015 9:55pm': 'So.....who is still here? ',
 '01/13/2018 8:51pm': 'I miss all my ads, now I see the feeds of actual people :( ',
 '01/14/2018 5:50pm': 'Happy birthday old man ',
 '01/16/2017 2:50pm': 'Happy MLK jr day ',
 '01/18/2014 2:56pm': 'Back to freezing my ass off 24/7 ',
 '01/19/2014 12:35pm': 'sucks that I have to cook as soon as I get back just because of my teeth ',
 '01/20/2014 6:55pm': 'Happy birthday big boi! ',
 '01/20/2015 6:13am': 'Happy Birthday Bro! ',
 